# 0. Install

เราจะต้อง Install kaggle เพื่อ Download Dataset และ geopandas เพื่อใช้ในการวิเคราะห์ข้อมูล geospatial (ถ้ายังไม่ได้ Install ให้ uncomment)

In [0]:
! pip install geopandas
! pip install kaggle --upgrade

# 1. Mount Google Drive

กำหนด path ของ Config File และ Dataset

In [0]:
config_path = '/content/drive'
dataset = 'alexisbcook/geospatial-learn-course-data'
data_path = '/content/datasets/' + dataset

Mount Google Drive เพื่อดึง Config File มาจาก Google Drive ส่วนตัวของเรา เมื่อเรารัน Cell ด้านล่างจะมีลิงค์ปรากฎขึ้นมาให้เรา Login กด Approve แล้ว Copy Authorization Code มาใส่ในช่องด้านล่าง แล้วกด Enter

In [0]:
from google.colab import drive
drive.mount(config_path)

# 2. Download Dataset

กำหนด Environment Variable ไปยังโฟลเดอร์ที่เก็บ kaggle.json

In [0]:
import os
os.environ['KAGGLE_CONFIG_DIR'] = f"{config_path}/My Drive/.kaggle"

สั่งดาวน์โหลด Dataset พร้อมทั้ง unzip ไว้ใน data_path

In [0]:
!kaggle datasets download {dataset} -p "{data_path}" --unzip

# 3. Import Library

Import folium Library เพื่อใช้ในการพล็อตแผนที่แบบ Interactive

In [0]:
import pandas as pd
import geopandas as gpd

import folium
from folium import Choropleth, Circle
from folium.plugins import HeatMap

# 4. Data

ใน ep นี้ 

In [21]:
plate_boundaries = gpd.read_file("./datasets/alexisbcook/geospatial-learn-course-data/Plate_Boundaries/Plate_Boundaries/Plate_Boundaries.shp")
plate_boundaries['coordinates'] = plate_boundaries.apply(lambda x: [(b,a) for (a,b) in list(x.geometry.coords)], axis='columns')
plate_boundaries.drop('geometry', axis=1, inplace=True)

plate_boundaries.head()

HAZ_PLATES  ...                                        coordinates
0     TRENCH  ...  [(-5.444200361999947, 133.6808931800001), (-5....
1     TRENCH  ...  [(-7.760600482999962, 125.47879802900002), (-7...
2     TRENCH  ...  [(19.817899819000047, 120.09999798800004), (19...
3     TRENCH  ...  [(26.175899215000072, 143.20620700100005), (26...
4     TRENCH  ...  [(0.41880004000006466, 132.8273013480001), (0....

[5 rows x 5 columns]

In [22]:
earthquakes = pd.read_csv("./datasets/alexisbcook/geospatial-learn-course-data/earthquakes1970-2014.csv", parse_dates=["DateTime"])
earthquakes.head()

DateTime  Latitude  Longitude  ...  RMS  Source       EventID
0 1970-01-04 17:00:40.200    24.139    102.503  ...  0.0     NEI  1.970010e+09
1 1970-01-06 05:35:51.800    -9.628    151.458  ...  0.0     NEI  1.970011e+09
2 1970-01-08 17:12:39.100   -34.741    178.568  ...  0.0     NEI  1.970011e+09
3 1970-01-10 12:07:08.600     6.825    126.737  ...  0.0     NEI  1.970011e+09
4 1970-01-16 08:05:39.000    60.280   -152.660  ...  NaN      AK           NaN

[5 rows x 12 columns]

In [24]:
# Create a base map with plate boundaries
m_1 = folium.Map(location=[35,136], tiles='cartodbpositron', zoom_start=5)
for i in range(len(plate_boundaries)):
    folium.PolyLine(locations=plate_boundaries.coordinates.iloc[i], weight=2, color='black').add_to(m_1)

# Your code here: Add a heatmap to the map
# HeatMap(data=earthquakes[['Latitude', 'Longitude']], radius=20).add_to(m_1)
HeatMap(data=[earthquakes['Latitude'], earthquakes['Longitude']], radius=20).add_to(m_1)

# Show the map
m_1

In [26]:
# Create a base map with plate boundaries
m_2 = folium.Map(location=[35,136], tiles='cartodbpositron', zoom_start=5)
for i in range(len(plate_boundaries)):
    folium.PolyLine(locations=plate_boundaries.coordinates.iloc[i], weight=2, color='black').add_to(m_2)
    
earthquakes['marker_color'] = pd.cut(earthquakes['Depth'], bins=4, 
                              labels=['yellow', 'orange', 'red', 'purple'])

# Your code here: Add a map to visualize earthquake depth
for idx, e in earthquakes.iterrows():    
    Circle(location=[e['Latitude'], e['Longitude']], radius=5000, color=e['marker_color']).add_to(m_2)

m_2

Can you detect a relationship between proximity to a plate boundary and earthquake depth?  Does this pattern hold globally?  In Japan?

In the northern half of Japan, it does appear that earthquakes closer to plate boundaries tend to be shallower (and earthquakes farther from plate boundaries are deeper). This pattern is repeated in other locations, such as the western coast of South America. But, it does not hold everywhere (for instance, in China, Mongolia, and Russia).

# Credit

# Credit

* https://www.kaggle.com/alexisbcook/coordinate-reference-systems
* https://matplotlib.org/3.1.1/api/_as_gen/matplotlib.pyplot.plot.html
* https://www.bualabs.com/archives/751/multi-label-image-classification-satellite-imagery-deep-learning-machine-learning-image-classification-ep-5/
* http://geopandas.org/gallery/index.html
* https://en.wikipedia.org/wiki/List_of_South_American_countries_by_area
* https://epsg.io/3035

* https://www.kaggle.com/alexisbcook/coordinate-reference-systems
* https://matplotlib.org/3.1.1/api/_as_gen/matplotlib.pyplot.plot.html
* https://www.bualabs.com/archives/751/multi-label-image-classification-satellite-imagery-deep-learning-machine-learning-image-classification-ep-5/
* http://geopandas.org/gallery/index.html
* https://en.wikipedia.org/wiki/List_of_South_American_countries_by_area
* https://epsg.io/3035

Which prefectures have high population density?



In [0]:
prefectures = gpd.read_file("../input/geospatial-learn-course-data/japan-prefecture-boundaries/japan-prefecture-boundaries/japan-prefecture-boundaries.shp")
prefectures.set_index('prefecture', inplace=True)
prefectures.head()

In [0]:
# DataFrame containing population of each prefecture
population = pd.read_csv("../input/geospatial-learn-course-data/japan-prefecture-population.csv")
population.set_index('prefecture', inplace=True)

# Calculate area (in square kilometers) of each prefecture
area_sqkm = pd.Series(prefectures.geometry.to_crs(epsg=32654).area / 10**6, name='area_sqkm')
stats = population.join(area_sqkm)

# Add density (per square kilometer) of each prefecture
stats['density'] = stats["population"] / stats["area_sqkm"]
stats.head()

In [0]:
# Create a base map
m_3 = folium.Map(location=[35,136], tiles='cartodbpositron', zoom_start=5)

# Your code here: create a choropleth map to visualize population density
Choropleth(geo_data=prefectures.geometry.__geo_interface__, data=stats.density, key_on='feature.id', 
           fill_color='YlGnBu', 
           legend_name='population density').add_to(m_3)

# Uncomment to see a hint
#q_3.a.hint()

# View the map
embed_map(m_3, 'q_3.html')

Which three prefectures have relatively higher density than the others?  Are they spread throughout the country, or all located in roughly the same geographical region?  (*If you're unfamiliar with Japanese geography, you might find [this map](https://en.wikipedia.org/wiki/Prefectures_of_Japan) useful to answer the questions.)

Tokyo, Kanagawa, and Osaka have the highest population density. All of these prefectures are located in central Japan, and Tokyo and Kanagawa are adjacent.

4) Which high-density prefecture is prone to high-magnitude earthquakes?

In [0]:
# Create a base map
m_4 = folium.Map(location=[35,136], tiles='cartodbpositron', zoom_start=5)

# Your code here: create a map
Choropleth(geo_data=prefectures.geometry.__geo_interface__, data=stats.density, key_on='feature.id', 
           fill_color='BuPu', 
           legend_name='population density and earthquake magnitude').add_to(m_4)

earthquakes['marker_color'] = pd.cut(earthquakes['Magnitude'], bins=4, 
                              labels=['yellow', 'orange', 'red', 'purple'])

# Your code here: Add a map to visualize earthquake depth
for idx, e in earthquakes.iterrows():    
    Circle(location=[e['Latitude'], e['Longitude']], 
           popup=("{} ({})").format(e['Magnitude'],e['DateTime'].year),
           radius=e['Magnitude']**5.5,           
           color=e['marker_color']).add_to(m_4)


# Uncomment to see a hint
#q_4.a.hint()

# View the map
embed_map(m_4, 'q_4.html')

Which prefecture do you recommend for extra earthquake reinforcement?

While there's no clear, single answer to this question, there are a few reasonable options. Tokyo is by far the most densely populated prefecture and has also experienced a number of earthquakes. Osaka is relatively less densely populated, but experienced an earthquake that was relatively stronger than those near Tokyo. And, the long coast of Kanagawa (in addition to its high density and the historical proximity of strong earthquakes) might lead us to worry about the added potential tsunami risk.

# Credit

* https://www.kaggle.com/alexisbcook/interactive-maps
* https://python-visualization.github.io/folium/modules.html
* https://www.bualabs.com/archives/751/multi-label-image-classification-satellite-imagery-deep-learning-machine-learning-image-classification-ep-5/
* https://en.wikipedia.org/wiki/Prefectures_of_Japan
* 